### Importing and building the plotting functions

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import datetime as dt
import numpy as np
import plotly.express as px
import cufflinks as cf
import plotly.graph_objects as go

In [2]:
%matplotlib inline
pd.set_option('display.max_rows', 200)
pd.set_option('display.max_columns', 20)
plt.style.use('fivethirtyeight')
# plt.style.use('seaborn')

from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)
cf.go_offline()

In [3]:
help(px.line)

Help on function line in module plotly.express._chart_types:

line(data_frame=None, x=None, y=None, line_group=None, color=None, line_dash=None, symbol=None, hover_name=None, hover_data=None, custom_data=None, text=None, facet_row=None, facet_col=None, facet_col_wrap=0, facet_row_spacing=None, facet_col_spacing=None, error_x=None, error_x_minus=None, error_y=None, error_y_minus=None, animation_frame=None, animation_group=None, category_orders=None, labels=None, orientation=None, color_discrete_sequence=None, color_discrete_map=None, line_dash_sequence=None, line_dash_map=None, symbol_sequence=None, symbol_map=None, markers=False, log_x=False, log_y=False, range_x=None, range_y=None, line_shape=None, render_mode='auto', title=None, template=None, width=None, height=None)
        In a 2D line plot, each row of `data_frame` is represented as vertex of
        a polyline mark in 2D space.
        
    Parameters
    ----------
    data_frame: DataFrame or array-like or dict
        This ar

In [4]:
def plotter(DF, name, xlabel= 'Date', scale = 'log', col = 'imp'):
    return px.line(
        DF, 
        x = DF.index, 
        y = Countries, 
        labels = {'x': xlabel, 'y': name}, 
        title = name+' wrt Date in Countries', 
        log_y = True if scale=='log' else False, 
        template = 'plotly_dark',
    )

In [5]:
def plotwrtDeaths(DF2, name1, DF, name2 = 'Deaths', scale = 'log', col = 'imp'):
    fig = go.Figure()
    
#     plt.ylim(bottom=0.05, top=2*10**4)
    
    columns = DF.columns if col == 'all' else Countries[::-1]
    for col in columns:
        fig.add_trace(
            go.Scatter(
                x = DF[col], 
                y = DF2[col], 
                mode = 'lines', 
                name = col,
            )
        )
    
    fig.update_xaxes(type= scale)
    fig.update_yaxes(type= scale)
    
    return fig.update_layout(title = f'{name1} wrt {name2} in Countries', 
                  xaxis_title = name2, 
                  yaxis_title = name1
                 )

In [22]:
def stackplotter(DF, name, tail=None):
    plt.figure(figsize = (14, 7))
    
    if tail:
        DF = DF.tail(tail)
    columns = Countries[::-1]
#     columns = DF.columns
    columns = [t for t in columns if 'World' not in t][::-1]
    DF['Rest of Earth'] = DF.World
    for col in columns:
        DF['Rest of Earth'] -= DF[col]
        
    columns.append('Rest of Earth')
    
    
    
    return px.area(
        DF, 
        x = DF.index, 
        y = columns, 
        labels = {'x': 'Date', 'y': name}, 
        title = name+' wrt Date in Countries', 
        template = 'plotly_dark',
    )

### Importing the Data from Johns Hopkins data

In [7]:
data_url = 'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_deaths_global.csv'
DF = pd.read_csv(data_url)

In [8]:
DF = DF.groupby('Country/Region').sum()
DF = DF.drop(columns = ['Lat', 'Long']).transpose()
DF['World'] = DF.sum(axis = 1)
DF = DF.rename(columns = {'United Kingdom': 'UK', 'Korea, South': 'S.Korea', 'Country/Region': 'Date'})
DF.index = pd.to_datetime(DF.index, format = '%m/%d/%y')
# DF.index.rename('Date', inplace = True)

Deaths = DF.copy()

In [9]:
data_url = 'https://raw.githubusercontent.com/CSSEGISandData/COVID-19/master/csse_covid_19_data/csse_covid_19_time_series/time_series_covid19_confirmed_global.csv'
DF = pd.read_csv(data_url)

In [10]:
DF = DF.groupby('Country/Region').sum()
DF = DF.drop(columns = ['Lat', 'Long']).transpose()
DF['World'] = DF.sum(axis = 1)
DF = DF.rename(columns = {'United Kingdom': 'UK', 'Korea, South': 'S.Korea', 'Country/Region': 'Date'})
DF.index = pd.to_datetime(DF.index, format = '%m/%d/%y')
# DF.index.rename('Date', inplace = True)

Confirmed = DF.copy()

In [11]:
colors = {'India': 'Blue', 
          'World': 'Blue', 
          'US': 'Black', 
          'Brazil': 'darkgreen', 
          'Mexico': 'Orange', 
          'UK': 'Purple', 
          'Italy': 'grey', 
          'Russia': 'cyan', 
          'France': 'violet', 
          'Germany': 'lime', 
          'Spain': 'teal',
          'Colombia': 'lightgreen', 
#           'Argentina': 'Teal',
          'Iran': 'brown', 
          'China': 'red', 
          'Peru': 'yellow'
         }

Countries = list(colors.keys())

### Deaths

In [12]:
Deaths[Countries].tail(5)

Country/Region   India    World      US  Brazil  Mexico      UK   Italy  \
2021-09-17      444529  4679137  672635  589573  270538  135314  130233   
2021-09-18      444838  4685838  673472  590508  270538  135478  130284   
2021-09-19      445133  4691849  673774  590752  271503  135539  130310   
2021-09-20      445385  4700003  676076  590955  271765  135589  130354   
2021-09-21      445768  4709101  678407  591440  272580  135793  130421   

Country/Region  Russia  France  Germany  Spain  Colombia    Iran  China  \
2021-09-17      193111  116618    92928  85783    125826  116436   4849   
2021-09-18      193891  116662    92964  85783    125860  116791   4849   
2021-09-19      194671  116696    92977  85783    125895  117182   4849   
2021-09-20      195438  116765    93058  85901    125924  117526   4849   
2021-09-21      196235  116901    93129  85983    125962  117905   4849   

Country/Region    Peru  
2021-09-17      198891  
2021-09-18      198976  
2021-09-19      199066  
2021-09-20      199036  
2021-09-21      199060

In [13]:
plotter(Deaths, 'Deaths')

### Confirmed Cases

In [14]:
Daily_Confirmed = np.round((Confirmed - Confirmed.shift(1))/1)
Daily_Confirmed = Daily_Confirmed.fillna(0).astype('int')
Daily_Confirmed[Countries].tail(5)

Country/Region  India   World      US  Brazil  Mexico     UK  Italy  Russia  \
2021-09-17      35662  593099  207886   11202    3754  32566   4544   19589   
2021-09-18      30773  532986   56849  150106       0  29476   4576   19999   
2021-09-19      30256  358548   37533    9458   16694  29298   3836   19825   
2021-09-20      26115  540395  201648    7884    3367  35943   2405   19376   
2021-09-21      26964  468694  120788    -573   12521  31188   3374   18796   

Country/Region  France  Germany  Spain  Colombia   Iran  China  Peru  
2021-09-17        7756     9904   3222      1544  17605     49     0  
2021-09-18        7972     7103      0      1655  12847     71  2039  
2021-09-19        5944     5667      0      1813  15975     52   589  
2021-09-20        1547     5328   5988      1185  17397     77   644  
2021-09-21        8776     7277   2450      1373  17564     42   779

In [15]:
Confirmed_EWM = np.round(Daily_Confirmed.ewm(com=14).mean().astype(int))
Confirmed_EWM[Countries].tail()

Country/Region  India   World      US  Brazil  Mexico     UK  Italy  Russia  \
2021-09-17      35551  587708  152379   20542   12192  32657   5249   18832   
2021-09-18      35232  584060  146010   29180   11379  32445   5204   18910   
2021-09-19      34900  569026  138778   27865   11733  32235   5113   18971   
2021-09-20      34315  567117  142969   26533   11176  32483   4932   18998   
2021-09-21      33824  560556  141491   24726   11265  32396   4828   18984   

Country/Region  France  Germany  Spain  Colombia   Iran  China  Peru  
2021-09-17       12741     9093   6449      2537  26011     50   917  
2021-09-18       12423     8961   6019      2478  25133     51   992  
2021-09-19       11991     8741   5618      2434  24522     51   965  
2021-09-20       11295     8513   5642      2350  24047     53   944  
2021-09-21       11127     8431   5430      2285  23615     52   933

In [16]:
plotter(Confirmed, 'Confirmed')

### Daily Deaths

In [17]:
Daily_Deaths = np.round((Deaths - Deaths.shift(1))/1)
Daily_Deaths = Daily_Deaths.fillna(0).astype('int')
Daily_Deaths[Countries].tail(5)

Country/Region  India  World    US  Brazil  Mexico   UK  Italy  Russia  \
2021-09-17        281   8608  2362     327     190  180     66     771   
2021-09-18        309   6701   837     935       0  164     51     780   
2021-09-19        295   6011   302     244     965   61     26     780   
2021-09-20        252   8154  2302     203     262   50     44     767   
2021-09-21        383   9098  2331     485     815  204     67     797   

Country/Region  France  Germany  Spain  Colombia  Iran  China  Peru  
2021-09-17         107       22     44        44   364      0     0  
2021-09-18          44       36      0        34   355      0    85  
2021-09-19          34       13      0        35   391      0    90  
2021-09-20          69       81    118        29   344      0   -30  
2021-09-21         136       71     82        38   379      0    24

### Exponential Weighted Mean

In [18]:
EWM = np.round(Daily_Deaths.ewm(com=7).mean(), 2)
name = 'Exponential Weighted Mean Weekly'

Weekly_Avg = np.round((Deaths - Deaths.shift(7))/7, 2)
# name = 'Weekly Average Deaths'

AVG = EWM 
# AVG = Weekly_Avg
AVG[Countries].tail(5)

Country/Region   India    World       US  Brazil  Mexico      UK  Italy  \
2021-09-17      332.43  9258.48  1964.56  546.95  597.26  143.64  59.28   
2021-09-18      329.50  8938.80  1823.61  595.46  522.60  146.19  58.24   
2021-09-19      325.19  8572.82  1633.41  551.52  577.90  135.54  54.21   
2021-09-20      316.04  8520.47  1716.98  507.96  538.42  124.85  52.94   
2021-09-21      324.41  8592.66  1793.74  505.09  572.99  134.74  54.69   

Country/Region  Russia  France  Germany  Spain  Colombia    Iran  China   Peru  
2021-09-17      768.80   95.14    43.45  82.76     50.59  482.40   0.07  33.45  
2021-09-18      770.20   88.75    42.52  72.41     48.52  466.47   0.06  39.89  
2021-09-19      771.43   81.91    38.83  63.36     46.83  457.04   0.06  46.16  
2021-09-20      770.87   80.29    44.10  70.19     44.60  442.91   0.05  36.64  
2021-09-21      774.14   87.26    47.46  71.67     43.77  434.92   0.04  35.06

In [19]:
plotter(np.round(AVG), name)

In [20]:
plotwrtDeaths(np.round(AVG, 1), name, Deaths)

### Stack Plots

In [23]:
stackplotter(AVG, name)

<Figure size 1008x504 with 0 Axes>

In [24]:
stackplotter(AVG.divide(AVG.World, axis=0), 'Deaths Percentage')

<Figure size 1008x504 with 0 Axes>

### Reproductivity

In [25]:
Reproductivity = np.round(EWM/EWM.shift(14), 4).clip(lower= 0.1)
Reproductivity[EWM.shift(14) < 12] = 1

In [26]:
plotter(Reproductivity, 'RF')

### Test rate

In [27]:
# We take the mortality to be 0.5%

mortality = 0.005

Testrate = np.round(Confirmed_EWM/(EWM/mortality), 3)
Testrate[EWM < 12] = None

In [28]:
plotter(Testrate, 'Test Rate', scale= 'log')

### Time Adjusted for starting day

In [29]:
def adjust_days(DF):
    X = DF.copy()
#     X.reset_index()
    for col in DF.columns:
        L = list(DF[Deaths[col]>5][col])
        X[col] = L + [None for _ in range(len(X[col]) - len(L))]
    return X.reset_index()[DF.columns]
xlabel= 'Days from 5 Deaths'

In [30]:
RF_A = adjust_days(Reproductivity)
plotter(RF_A, 'Reproductivity', xlabel)

KeyError: 'Rest of Earth'

In [ ]:
AVG_A = adjust_days(AVG)
plotter(np.round(AVG_A), 'Average Deaths', xlabel)

In [ ]:
Deaths_A = adjust_days(Deaths)
plotter(Deaths_A, 'Deaths', xlabel)

### Today's Statistics by combining the previous tables

In [ ]:
LastDay_DF = pd.DataFrame()
LastDay_DF['Country'] = Deaths.columns
LastDay_DF = LastDay_DF.set_index('Country')

D = {
    'Deaths':Deaths,
    'Daily_Deaths':Daily_Deaths,
    'Weekly_Deaths': Weekly_Avg,
    'EWM7': EWM,
    'Reproductivity':Reproductivity,
    'Confirmed': Confirmed, 
    'Testrate': Testrate,
    'Confirmed_EWM': Confirmed_EWM
    }
for name in D:
    LastDay_DF[name] = D[name].iloc[-1]
LastDay_DF['Estimated(M)'] = np.round((LastDay_DF.Deaths/mortality)/1000000, 2)

In [ ]:
LastDay_DF.sort_values('Deaths', ascending = False).head(12)

In [ ]:
LastDay_DF.sort_values('Weekly_Deaths', ascending = False).head(12)

### Pie Chart

In [ ]:
def piechart(name='Deaths', size=12, DF=LastDay_DF):
    plt.figure(figsize = (size, size))
    DF = DF.sort_values(name, ascending = False)
    
    countries = DF.index[1:]
    deaths = DF[name][1:].clip(0, None)
    
    print ('World total: ',int( DF.loc['World'][name]))
    
    plt.pie(deaths, 
            labels= [c +' '+ str(d) for c, d in zip(countries, deaths)], 
            startangle=90,
            counterclock=False,
            autopct='%1.f%%', 
#             pctdistance=0.8
           )
    
    plt.title(name+' piechart for every country')

In [ ]:
piechart('Deaths')

In [ ]:
piechart('Weekly_Deaths')

In [ ]:
piechart('Daily_Deaths')

In [ ]:
print('Today\'s Date: ', dt.datetime.now().date())

In [ ]:
# Total estimated Cases: 
LastDay_DF.loc['World'].Deaths/mortality

<p>Per Capita deaths are included in this  <a href="https://www.statista.com/statistics/1104709/coronavirus-deaths-worldwide-per-million-inhabitants/" rel="nofollow">Statista</a></p>

In [ ]:
!git add .
!git commit -m "`date` update"
!git push origin master